In [ ]:
import lstm_ts
import time
import warnings
import torch

dtype = torch.FloatTensor
ltype = torch.LongTensor

In [ ]:
# Seed random number generator to get reproducible results.
torch.manual_seed(1)

global_start_time = time.time()

# Set hyper-parameters.
num_epochs  = 20 # try it with 20.
seq_len = 50
decay = 0
learning_rate = 0.01
batch_size = 512

In [ ]:
print('Loading data... ')

X_train, y_train, X_test, y_test = lstm_ts.load_data('sine_wave.csv', seq_len) # True

print('Data Loaded.')

In [ ]:
model = lstm_ts.LSTMTimeSeries([1, 50, 100, 1])
loss_fn = torch.nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), 
                             lr = learning_rate, weight_decay = decay)

for epoch in range(num_epochs):
    # Go over minibatches.
    j = 0
    cost = 0
    while batch_size * (j + 1) <= X_train.shape[0]:
        Xb_train = torch.tensor(X_train[batch_size * j: batch_size * (j + 1)]).type(dtype)
        yb_train = torch.tensor(y_train[batch_size * j: batch_size * (j + 1)]).type(dtype)

        # Forward propagation.
        y_pred = model(Xb_train)

        # Compute loss.
        loss = loss_fn(y_pred, yb_train)

        # Zero the gradients.
        optimizer.zero_grad()

        # Use autograd to compute gradient with respect to model params.
        loss.backward()
    
        # Update weights.
        optimizer.step()

        cost += loss.data.item()
        j += 1
        
    print("Epoch %d: average cost %f" % (epoch, cost / j))

print('Training duration (s) : ', time.time() - global_start_time)

In [ ]:
predicted = model.predict_sequence_full(X_test, seq_len)
# predicted = model.predict_point_by_point(X_test)        

import lstm_ts
lstm_ts.plot_results(predicted, y_test)

## Try it on $\frac{sin(x)}{\sqrt{x}}$

## Try it on $sin(x) + N(0,0.05)$